In [3]:
import gym
import numpy as np
import math
import random

In [4]:
env = gym.make('CartPole-v0')

In [5]:
env.action_space.n

2

In [6]:
env.observation_space

Box(4,)

In [7]:
env.observation_space.low

array([-4.8000002e+00, -3.4028235e+38, -4.1887903e-01, -3.4028235e+38],
      dtype=float32)

In [8]:
env.observation_space.high

array([4.8000002e+00, 3.4028235e+38, 4.1887903e-01, 3.4028235e+38],
      dtype=float32)

In [9]:
NUM_BUCKETS = (1, 1, 6, 3)

In [10]:
NUM_ACTIONS = env.action_space.n

In [11]:
STATE_BOUNDS = list(zip(env.observation_space.low, env.observation_space.high))

In [12]:
STATE_BOUNDS[1] = [-0.5, 0.5]

In [13]:
STATE_BOUNDS[3] = [-math.radians(50), math.radians(50)]

In [14]:
STATE_BOUNDS

[(-4.8, 4.8),
 [-0.5, 0.5],
 (-0.41887903, 0.41887903),
 [-0.8726646259971648, 0.8726646259971648]]

In [15]:
q_table = np.zeros(NUM_BUCKETS + (NUM_ACTIONS,))

In [16]:
q_table.shape

(1, 1, 6, 3, 2)

In [17]:
q_table.size

36

In [18]:
EXPLORE_RATE_MIN = 0.01

In [19]:
LEARNING_RATE_MIN = 0.1

In [20]:
def get_explore_rate(t):
    return max(EXPLORE_RATE_MIN, min(1, 1.0-math.log10((t+1)/25)))

In [21]:
def get_learning_rate(t):
    return max(LEARNING_RATE_MIN, min(0.5, 1.0-math.log10((t+1)/25)))

In [22]:
def select_action(state, explore_rate):
    if random.random() < explore_rate:
        action = env.action_space.sample()
    else:
        action = np.argmax(q_table[state])
    return action

In [23]:
def state_to_bucket(state):
    
    bucket_indices = []
    
    for i in range(len(state)):
        if state[i] <= STATE_BOUNDS[i][0]:
            bucket_index = 0
            
        elif state[i] >= STATE_BOUNDS[i][1]:
            bucket_index = NUM_BUCKETS[i] - 1
        
        else:
            bound_width = STATE_BOUNDS[i][1] - STATE_BOUNDS[i][0]
            
            offset = (NUM_BUCKETS[i] - 1) * STATE_BOUNDS[i][0] / bound_width
            scaling = (NUM_BUCKETS[i] - 1) / bound_width
            
            bucket_index = int(round(scaling * state[i] - offset))
        
        bucket_indices.append(bucket_index)
    
    return tuple(bucket_indices)

In [24]:
def simulate():
    
    learning_rate = get_learning_rate(0)
    explore_rate = get_explore_rate(0)
    
    discount_factor = 0.99
    num_streaks = 0
    
    for episode in range(1000):
        
        observ = env.reset()
        
        state_0 = state_to_bucket(observ)
        
        for t in range(250):
            
            env.render()
            
            action = select_action(state_0, explore_rate)
            
            observ, reward, done, _ = env.step(action)
            
            state = state_to_bucket(observ)
            
            best_q = np.amax(q_table[state])
            
            q_table[state_0 + (action,)] += learning_rate * (reward + discount_factor*(best_q) - q_table[state_0 + (action,)])
            
            
            state_0 = state
            
            print("\nEpisode = %d" % episode)
            print("t = %d" % t)
            print("Action: %d" % action)
            print("State: %s" %str(state))
            print("Reward: %f" % reward)
            print("Best Q: %f" % best_q)
            print("Explore rate: %f" % explore_rate)
            print("Learning rate: %f" % learning_rate)
            print("Streaks: %d" %num_streaks)
            
            print("")
            
            if done:
                print("Episode %d finished after %f time steps" % (episode, t))
                
                if (t >= 199):
                    num_streaks += 1
                else:
                    num_streaks = 0
                break
            
            if num_streaks > 120:
                break
            
            explore_rate = get_explore_rate(episode)
            learning_rate = get_learning_rate(episode)

In [25]:
simulate()


Episode = 0
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 0.000000
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 0
t = 1
Action: 1
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 0.500000
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 0
t = 2
Action: 1
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 0.747500
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 0
t = 3
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 0.000000
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 0
t = 4
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 1.121881
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 0
t = 5
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 1.055331
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 0
t = 6
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 1.583330
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episo

Streaks: 0


Episode = 3
t = 6
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 3.859592
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 3
t = 7
Action: 0
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 4.340294
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 3
t = 8
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 4.340294
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 3
t = 9
Action: 0
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 4.818592
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 3
t = 10
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 5.018362
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 3
t = 11
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 5.393385
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 3
t = 12
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 5.866418
Explore rate: 1.000000
Learning rate: 0.500000
Str

State: (0, 0, 4, 2)
Reward: 1.000000
Best Q: 2.830703
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 6
t = 22
Action: 0
State: (0, 0, 4, 2)
Reward: 1.000000
Best Q: 2.830703
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0

Episode 6 finished after 22.000000 time steps

Episode = 7
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 4.531920
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 7
t = 1
Action: 0
State: (0, 0, 2, 2)
Reward: 1.000000
Best Q: 1.563591
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 7
t = 2
Action: 1
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 4.531920
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 7
t = 3
Action: 0
State: (0, 0, 2, 2)
Reward: 1.000000
Best Q: 3.525096
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 7
t = 4
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 8.492606
Explore rate: 1.000000
Learning rate: 0.500000



Episode = 9
t = 5
Action: 1
State: (0, 0, 3, 2)
Reward: 1.000000
Best Q: 12.308912
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 9
t = 6
Action: 0
State: (0, 0, 3, 2)
Reward: 1.000000
Best Q: 12.308912
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 9
t = 7
Action: 0
State: (0, 0, 3, 2)
Reward: 1.000000
Best Q: 12.747368
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 9
t = 8
Action: 0
State: (0, 0, 4, 2)
Reward: 1.000000
Best Q: 3.919017
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 9
t = 9
Action: 0
State: (0, 0, 4, 2)
Reward: 1.000000
Best Q: 3.919017
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0

Episode 9 finished after 9.000000 time steps

Episode = 10
t = 0
Action: 0
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 9.682785
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 10
t = 1
Action: 0
State: (0, 0, 3, 2)
Reward: 1.000000
Best Q: 10.136436
Explore rate: 



Episode = 13
t = 3
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 12.535417
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 13
t = 4
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 12.535417
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 13
t = 5
Action: 1
State: (0, 0, 2, 0)
Reward: 1.000000
Best Q: 12.802933
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 13
t = 6
Action: 0
State: (0, 0, 1, 0)
Reward: 1.000000
Best Q: 3.684177
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 13
t = 7
Action: 1
State: (0, 0, 1, 0)
Reward: 1.000000
Best Q: 3.684177
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0


Episode = 13
t = 8
Action: 0
State: (0, 0, 1, 0)
Reward: 1.000000
Best Q: 4.045294
Explore rate: 1.000000
Learning rate: 0.500000
Streaks: 0

Episode 13 finished after 8.000000 time steps

Episode = 14
t = 0
Action: 0
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 13.327278
Explore

...


Episode = 707
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.893917
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 708
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.892370
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 709
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.894023
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 710
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.894129
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 711
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.892477
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 712
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.894235
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 713
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.894341
Explore rate: 0.010000
Learning 


Episode = 768
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.897670
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 769
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.897772
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 770
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.897874
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 771
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.895028
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 772
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.895133
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 773
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.897976
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 774
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.898078
Explore rate: 0.010000
Learning 


Episode = 827
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.898438
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 828
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.900123
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 829
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.898539
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 830
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.900223
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 831
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.898641
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 832
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.898742
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 833
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.898843
Explore rate: 0.010000
Learning 


Episode = 888
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.903270
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 889
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.903367
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 890
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.903463
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 891
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.901243
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 892
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.901342
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 893
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.901441
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 894
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.901539
Explore rate: 0.010000
Learning 


Episode = 948
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.904546
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 949
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.905754
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 950
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.905848
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 951
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.905942
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 952
t = 0
Action: 0
State: (0, 0, 2, 1)
Reward: 1.000000
Best Q: 99.904642
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 953
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.906036
Explore rate: 0.010000
Learning rate: 0.100000
Streaks: 121


Episode = 954
t = 0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.000000
Best Q: 99.906130
Explore rate: 0.010000
Learning 

In [26]:
env.close()

In [27]:
print(q_table)

[[[[[ 0.          0.        ]
    [ 0.          0.        ]
    [ 0.          0.        ]]

   [[42.87897538 35.44152698]
    [42.93972189 43.80824446]
    [33.52650566 35.1392959 ]]

   [[99.86048061 99.19218741]
    [99.9071832  99.80427399]
    [99.67535042 99.86494091]]

   [[99.86541011 99.65018973]
    [99.79847777 99.90799   ]
    [99.24902526 99.86130561]]

   [[ 0.          5.08679488]
    [25.31649955  7.30859622]
    [28.81056622 28.73548103]]

   [[ 0.          0.        ]
    [ 0.          0.        ]
    [ 0.          0.        ]]]]]
